### Preparation 

In [1]:
import os, sys
from glob import glob

import pandas as pd
import numpy as np
import datetime as dt

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

from util import *

pd.set_option("display.max_columns", None)
data_dir = os.path.join("Data")
fig_dir = os.path.join("Figures")
table_dir = os.path.join("Tables")

In [2]:
bout_df = []
for file in glob(os.path.join(data_dir, "Bout", "*.csv")):
    uid = os.path.splitext(os.path.basename(file))[0]
    tmp = pd.read_csv(file, header = 0, index_col= None)
    tmp["UID"] = [uid] * tmp.shape[0]
    bout_df.append(tmp)
bout_df = pd.concat(bout_df,axis = 0)
display(bout_df.head())

START            END  UTC       READABLE_START  \
0  1636670760000  1636670820000    9  2021-11-12 07:46:00   
1  1636670880000  1636671000000    9  2021-11-12 07:48:00   
2  1636672140000  1636672320000    9  2021-11-12 08:09:00   
3  1636672380000  1636672560000    9  2021-11-12 08:13:00   
4  1636672680000  1636672740000    9  2021-11-12 08:18:00   

          READABLE_END  PHONE_STEP  WEARABLE_STEP  AVERAGE_STEP  DURATION  \
0  2021-11-12 07:47:00        38.0           12.0          25.0         1   
1  2021-11-12 07:50:00        21.0            0.0          21.0         2   
2  2021-11-12 08:12:00         0.0           32.0          32.0         3   
3  2021-11-12 08:16:00         0.0           86.0          86.0         3   
4  2021-11-12 08:19:00        22.0            0.0          22.0         1   

       TYPE   UID  
0      BOTH  P077  
1     PHONE  P077  
2  WEARABLE  P077  
3  WEARABLE  P077  
4     PHONE  P077

### Both-Tracked Bout Comparison
*Is there a significant difference between the number of steps measured by smartphones and those measured through wearables when both devices measure the number of steps?*

In [3]:
both_bout = bout_df.query("TYPE == 'BOTH'")
print("Correlation Coef: rho = {:.03f}".format(both_bout.corr(numeric_only = True).loc["PHONE_STEP","WEARABLE_STEP"]))

Correlation Coef: rho = 0.995


### Single Variable Comparison

#### Depending on User

In [27]:
user_coverage = bout_df.groupby(["UID","TYPE"]).agg(STEP = ("AVERAGE_STEP","sum")).unstack(level = 1)
user_coverage = user_coverage.apply(lambda x: x/np.sum(x), axis = 1)
user_coverage.columns = user_coverage.columns.get_level_values(1)

In [34]:
user_coverage.sort_values(by = ["BOTH","PHONE"], inplace= True, ascending= False)
fig = go.Figure()
for device in ["BOTH","PHONE","WEARABLE"]:
    fig.add_trace(
        go.Bar(x = user_coverage.index, y = user_coverage[device].values, name = device,  marker_color = colors[device])
    )
fig.update_layout(
    width = 1200,
    height = 600,
    xaxis = dict(
        title = "Steps Per Walking Bout", 
        tickmode = 'array', 
        tickvals = np.arange(user_coverage.shape[0]), 
        ticktext = user_coverage.index,
        tickangle = 45,
    ),
    barmode = 'stack',
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.1),
)
fig.show()
fig.write_image(os.path.join(fig_dir,"comparison_across_user.svg"))

#### Intensity of Walking Bouts
*Does the coverage of each device change depending on the intensity of the step-based activity?*
* Intensity of each walking bouts was calculated by Steps Per Minute (SPM)
    * MPA, Moderate Physical Activity: \[0, 100\)
    * MVPA, Moderate to Vigorous Physical Activity: \[100, 133\)
    * VPA, Vigorous Physical Activity: \[133, \)

In [4]:
bout_df["SPM"] = bout_df["AVERAGE_STEP"].values / bout_df["DURATION"].values
bout_df["PA_TYPE"] = [calcIntensity(spm) for spm in bout_df["SPM"].values]

In [5]:
tmp = bout_df.groupby(["TYPE","PA_TYPE"]).agg(STEP = ("AVERAGE_STEP","sum"))
tmp = tmp[['STEP']].unstack(level = 0)
tmp.columns = tmp.columns.get_level_values(1)
tmp = tmp.apply(lambda x: x/np.sum(x), axis = 1)
display(tmp)
tmp.to_csv(os.path.join(table_dir, "activity_intensity.csv"))

TYPE         BOTH     PHONE  WEARABLE
PA_TYPE                              
MPA      0.609791  0.222982  0.167227
MVPA     0.766090  0.134710  0.099200
VPA      0.555880  0.007434  0.436686

#### Steps Per Bouts
*Does the coverage of each device change depending on the duration of the step-based activity?*

In [6]:
def calcLevel(STEP):
    return STEP // 20
bout_df["STEP_LEVEL"] = [calcLevel(STEP) for STEP in bout_df["AVERAGE_STEP"].values]

In [7]:
tmp = bout_df.groupby(["TYPE","STEP_LEVEL"]).agg(STEP = ("AVERAGE_STEP","sum"), CNT = ("AVERAGE_STEP", "count"))
# Remove some duration with only few bouts
tmp.query("CNT > 20", inplace = True)
tmp = tmp[['STEP']].unstack(level = 0, fill_value = 0)
tmp.columns = tmp.columns.get_level_values(1)
tmp = tmp.apply(lambda x: x/np.sum(x), axis = 1) * 100

fig = go.Figure()
for device in ["BOTH","PHONE","WEARABLE"]:
    fig.add_trace(
        go.Bar(x = np.arange(80), y = tmp[device].values[:80], name = device,  marker_color = colors[device])
    )
fig.update_layout(
    width = 1200,
    height = 600,
    xaxis = dict(
        title = "Steps Per Walking Bout", 
        tickmode = 'array', 
        tickvals = np.arange(80) + .5, 
        ticktext = np.arange(80) * 20,
        tickangle = 45,
    ),
    barmode = 'stack',
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.1),
)
fig.show()
fig.write_image(os.path.join(fig_dir,"comparison_step_per_bout.svg"))

#### Day of Week
*How does the coverage vary depending on the day of the week?*

In [8]:
bout_df["DATETIME"] = pd.to_datetime(bout_df["START"], unit = "ms") + pd.to_timedelta(bout_df["UTC"], unit = "h")
bout_df["DAY_OF_WEEK"] = bout_df["DATETIME"].dt.day_of_week
bout_df["DATE"] = bout_df["DATETIME"].dt.date
tmp = bout_df.groupby(["UID","DATE","DAY_OF_WEEK", "TYPE"]).agg(STEP = ("AVERAGE_STEP","sum"), CNT = ("AVERAGE_STEP","count"))
tmp = tmp[['STEP']].unstack(level = 3, fill_value = 0)
tmp = tmp.apply(lambda x: x/np.sum(x)*100, axis = 1)
tmp.columns = tmp.columns.get_level_values(1)
tmp.reset_index(inplace = True)
day_of_week = ["Mon","Tue","Wed","Thu","Fri","Sat","Sun"]
tmp["DAY_OF_WEEK_TEXT"] = [day_of_week[i] for i in tmp["DAY_OF_WEEK"]]
tmp.set_index(["UID","DATE","DAY_OF_WEEK", "DAY_OF_WEEK_TEXT"], inplace = True)
tmp.columns = pd.MultiIndex.from_product([["COVERAGE"], tmp.columns])
tmp = tmp.stack(level = 1)
tmp.reset_index(inplace= True)
fig = px.box(tmp, x="DAY_OF_WEEK_TEXT", y = "COVERAGE", color = "TYPE", color_discrete_map= colors)
fig.update_layout(
    xaxis =dict(title = "Day of Week"),
    yaxis = dict(title = "Coverage"),
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.1),
)
fig.show()
fig.write_image(os.path.join(fig_dir,"comparison_day_of_week.svg"))

#### Daily Step Count
*How does the coverage vary depending on the daily step count?*

In [9]:
tmp = bout_df.groupby(["UID","DATE","TYPE"]).agg(STEP = ("AVERAGE_STEP","sum"))
tmp = tmp.unstack(level = 2, fill_value = 0)
col = tmp.columns.get_level_values(1) 
tmp = tmp.apply(lambda x: [*x/np.sum(x)*100, np.sum(x)], axis = 1, result_type= 'expand')
tmp.columns = [*col, "DAILY_STEP"]
tmp.reset_index(inplace= True)
Q1, Q2, Q3 = np.percentile(tmp["DAILY_STEP"].values, [25,50,75])
def calcLevel(step):
    if step < Q1:
        return 0
    elif step < Q2:
        return 1
    elif step < Q3:
        return 2
    else:
        return 3
tmp["LEVEL"] = [calcLevel(step) for step in tmp["DAILY_STEP"]]
tmp.set_index(["UID","DATE","DAILY_STEP", "LEVEL"], inplace = True)
tmp.columns = pd.MultiIndex.from_product([["COVERAGE"], tmp.columns])
tmp.columns.set_names(level = 1,names = "TYPE", inplace = True)
tmp = tmp.stack(level = 1)
tmp.reset_index(inplace= True)
fig = px.box(tmp, x="LEVEL", y = "COVERAGE", color = "TYPE", color_discrete_map= colors)
fig.update_layout(
    xaxis =dict(title = "Daily Step Count", tickmode = "array", tickvals = list(range(4)), ticktext = [f"[0, {int(Q1)})", f"[{int(Q1)},{int(Q2)})", f"[{int(Q2)},{int(Q3)})", f"[{int(Q3)},)"]),
    yaxis = dict(title = "Coverage"),
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.1),
)
fig.show()
fig.write_image(os.path.join(fig_dir,"comparison_daily_step_count.svg"))

#### Time of Day
*How does the coverage vary depending on the time of day?*

We look for two plots: 
* Comparing coverage between daytime and night of each day.
* Average diurnal pattern of coverage through out the day.

In [10]:
def isNight(hour):
    return hour >= 19 or hour < 7
bout_df["HOUR"] = bout_df["DATETIME"].dt.hour
bout_df["NIGHT"] = [ isNight(hour) for hour in bout_df["HOUR"]]
tmp = bout_df.groupby(["UID","DATE","NIGHT", "TYPE"]).agg(STEP = ("AVERAGE_STEP","sum"))
tmp = tmp.unstack(level = 3, fill_value = 0)
tmp = tmp.apply(lambda x: x/np.sum(x)*100, axis = 1)
tmp.reset_index(inplace= True)
tmp.set_index(["UID","DATE","NIGHT"], inplace = True)
tmp = tmp.stack(level = 1)
tmp.reset_index(inplace= True)
fig = px.box(tmp, x="NIGHT", y = "STEP", color = "TYPE", color_discrete_map= colors)
fig.update_layout(
    xaxis =dict(title = "Time of Day", tickmode = "array", tickvals = list(range(2)), ticktext = ["Night(19 - 07)" , "Day(07 - 19)"]),
    yaxis = dict(title = "Coverage"),
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.1),
    width = 900
)
fig.show()
fig.write_image(os.path.join(fig_dir, "comparison_night_and_day.svg"))

In [11]:
dfs = []
for file in sorted(glob(os.path.join("Data", "Bout", "*.csv"))):
    uid = os.path.splitext(os.path.basename(file))[0]
    tmp = pd.read_csv(file, header=0, index_col=None)
    tmp["UID"] = [uid] * tmp.shape[0]
    tmp["DATETIME"] = pd.to_datetime(
        tmp["START"], unit='ms') + pd.to_timedelta(tmp["UTC"], unit="hour")
    tmp["DATE"] = tmp["DATETIME"].dt.date
    tmp["HOUR"] = tmp["DATETIME"].dt.hour

    tmp = tmp.groupby(["UID", "DATE", "HOUR", "TYPE"]).agg(
        STEP=('AVERAGE_STEP', 'sum'))
    tmp = tmp.reindex(
        pd.MultiIndex.from_product(
            [tmp.index.get_level_values(0).unique(), tmp.index.get_level_values(1).unique(), np.arange(24), tmp.index.get_level_values(3).unique()])
    )
    tmp.fillna(0, inplace = True)
    tmp = tmp.unstack(level=3, fill_value=0)

    columns = ["STEP", *tmp.columns.get_level_values(1)]
    tmp = tmp.apply(lambda x: [np.sum(x)/10, *(x/np.sum(x) *100)] if np.sum(x)!= 0 else [0, np.nan, np.nan, np.nan], axis = 1, result_type = "expand")
    tmp.columns = columns
    tmp = tmp.interpolate().bfill().ffill()
    
    tmp = tmp.unstack(level = 2)
    dfs.append(tmp)
diurnal_df = pd.concat(dfs, axis = 0)
diurnal_df.columns = ["_".join([a,str(b)]) for (a,b) in diurnal_df.columns]

In [12]:
fig = go.Figure()
for idx, device in enumerate(["BOTH","PHONE","WEARABLE"]):
    fig.add_trace(
        go.Scatter(
            x = np.arange(24), y = diurnal_df.iloc[:,(idx+1)*24: (idx+2)*24].values.mean(axis = 0), mode="lines+markers", name = device, marker=dict(color = colors[device])
        )
    )
fig.add_trace(
    go.Scatter(
        x = np.arange(24), y = diurnal_df.iloc[:,:24].values.mean(axis = 0), mode="lines+markers", name = "STEP", marker=dict(color = 'black')
    )
)
fig.update_layout(
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.1),
    xaxis= dict(range = [-1,25], tickmode = 'array', tickvals = np.arange(25), ticktext = [str(i).zfill(2) for i in range(25)]),
    yaxis = dict(range= [-5, 105], tickmode = 'array', tickvals = np.arange(6)*20, ticktext = np.arange(6)*20),
)
fig.write_image(os.path.join(fig_dir, "comparison_time_of_day.svg"))
fig.show()

### Diurnal Pattern Clustering

*How the major diurnal patterns look like?* 

In [13]:
from sklearn.cluster import KMeans

LABEL_ORDER = ["Both Dominant", "Phone to Both","Wearable Dominant", "Phone Dominant"]
DIURNAL_LABEL_IDX_TO_NAME = {0:"Wearable Dominant", 1: "Phone Dominant", 2: "Phone to Both", 3: "Both Dominant"}
DIURNAL_LABEL_NAME_TO_IDX = {v:k for k,v in DIURNAL_LABEL_IDX_TO_NAME.items()}

cluster_model = KMeans(n_clusters= 4, n_init=70, random_state=10170)
cluster_result = cluster_model.fit(diurnal_df.values[:, 24:24*4]).labels_

In [14]:
fig = make_subplots(
    cols = 2, rows = 2,
    subplot_titles = [val +" Pattern" for val in LABEL_ORDER],
    vertical_spacing = .15,
    horizontal_spacing = .05
)

for ldx, label in enumerate(LABEL_ORDER):
    jdx = DIURNAL_LABEL_NAME_TO_IDX[label]
    sample_idx = np.arange(diurnal_df.shape[0])[cluster_result == jdx]
    cluster_center = np.mean(diurnal_df.iloc[sample_idx].values, axis=0)
    for idx, col in enumerate(colors.keys()):
        filter = [val.startswith(col) for val in diurnal_df.columns]
        col_idx = np.arange(len(diurnal_df.columns))[filter]
        fig.append_trace(
            go.Scatter(x=np.arange(24) + .5,
                        y=cluster_center[col_idx], name=col, mode="lines+markers", showlegend=(ldx == 0), marker=dict(color=colors[col])), 
            row = (ldx+2)//2, col = ldx%2 +1
        )
fig.update_layout(
    width = 1200,
    height = 600,
    xaxis= dict(range = [-1,25], tickmode = 'array', tickvals = np.arange(9)*3, ticktext = [str(i).zfill(2) for i in np.arange(9)*3]),
    yaxis = dict(range= [-5, 105], tickmode = 'array', tickvals = np.arange(6)*20, ticktext = np.arange(6)*20),
    xaxis2= dict(range = [-1,25], tickmode = 'array', tickvals = np.arange(9)*3, ticktext = [str(i).zfill(2) for i in np.arange(9)*3]),
    yaxis2 = dict(range= [-5, 105], tickmode = 'array', tickvals = np.arange(6)*20, ticktext = np.arange(6)*20),
    xaxis3= dict(range = [-1,25], tickmode = 'array', tickvals = np.arange(9)*3, ticktext = [str(i).zfill(2) for i in np.arange(9)*3]),
    yaxis3 = dict(range= [-5, 105], tickmode = 'array', tickvals = np.arange(6)*20, ticktext = np.arange(6)*20),
    xaxis4= dict(range = [-1,25], tickmode = 'array', tickvals = np.arange(9)*3, ticktext = [str(i).zfill(2) for i in np.arange(9)*3]),
    yaxis4 = dict(range= [-5, 105], tickmode = 'array', tickvals = np.arange(6)*20, ticktext = np.arange(6)*20),
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.15, font_size = 14),
)
fig.show()
fig.write_image(os.path.join(fig_dir,"diurnal_pattern.svg"))

In [15]:
diurnal_df_ = diurnal_df.copy()
diurnal_df_["LABEL"] = [DIURNAL_LABEL_IDX_TO_NAME[i] for i in cluster_result]
diurnal_df_.reset_index(inplace = True)
diurnal_df_["WEEKEND"] = [val >= 5 for val in pd.to_datetime(diurnal_df_["DATE"]).dt.day_of_week]
diurnal_df_["DAILY_STEP"] = diurnal_df_.values[:,2:26].sum(axis = 1) * 10 # it was divided with 10 to adjust unit
pattern_stat = diurnal_df_.groupby(["LABEL"]).agg(
    AVG_DAILY_STEP = ("DAILY_STEP", "mean"), 
    QUARTILE_1ST_STEP = ("DAILY_STEP",lambda x: np.percentile(x, 25)),
    QUARTILE_2ND_STEP = ("DAILY_STEP",lambda x: np.percentile(x, 50)),
    QUARTILE_3RD_STEP = ("DAILY_STEP",lambda x: np.percentile(x, 75)),
    N_WEEKEND = ("WEEKEND","sum"), 
    N_DAY = ("DATE","count"),
    N_USER = ("UID","nunique"),)
pattern_stat["WEEKEND_RATIO"] = pattern_stat["N_WEEKEND"].values / pattern_stat["N_DAY"].values

In [16]:
pattern_stat.sort_index(key = lambda x: [LABEL_ORDER.index(val) for val in x], inplace = True)
display(pattern_stat)
pattern_stat.to_csv(os.path.join(table_dir,"diurnal_pattern_stat.csv"))

AVG_DAILY_STEP  QUARTILE_1ST_STEP  QUARTILE_2ND_STEP  \
LABEL                                                                     
Both Dominant         8659.047878           5184.375             7821.5   
Phone to Both         8490.021609           4553.500             7200.0   
Wearable Dominant     7009.716149           3596.500             6233.0   
Phone Dominant        4908.521338           1150.750             3906.5   

                   QUARTILE_3RD_STEP  N_WEEKEND  N_DAY  N_USER  WEEKEND_RATIO  
LABEL                                                                          
Both Dominant              10744.875        142    872      90       0.162844  
Phone to Both              10982.000        237    725      92       0.326897  
Wearable Dominant           9252.000        256    805      76       0.318012  
Phone Dominant              6942.500        320    760      79       0.421053

### User Group Clustering

In [17]:
user_diurnal_df = diurnal_df_.groupby(["UID","LABEL"]).agg(CNT = ("DATE","count"))
user_diurnal_df = user_diurnal_df.unstack(level = 1, fill_value= 0)
user_diurnal_df.columns = user_diurnal_df.columns.get_level_values(1)
user_diurnal_df = user_diurnal_df[LABEL_ORDER]
user_diurnal_df

LABEL  Both Dominant  Phone to Both  Wearable Dominant  Phone Dominant
UID                                                                   
P001               3             19                  1               8
P002              18              6                  0               7
P004               1              5                  1              24
P006               0              3                 27               1
P007               1              8                  7              15
...              ...            ...                ...             ...
P122               1             25                  0               5
P124              19              5                  1               6
P125               2              7                 10              12
P126               1             23                  1               6
P127              12              2                  2              15

[102 rows x 4 columns]

In [18]:
from sklearn.cluster import KMeans

cluster_model = KMeans(n_clusters= 4, n_init=70, random_state=10170)
cluster_result = cluster_model.fit(user_diurnal_df.values).labels_

In [19]:
user_diurnal_df_ = user_diurnal_df.copy()
user_diurnal_df_["LABEL"] = cluster_result
USER_GROUP_IDX_TO_NAME = {
    0: "Phone to Both",
    1: "Both Dominant",
    2: "Wearable Dominant",
    3: "Phone Dominant"
}
USER_GROUP_NAME_TO_IDX = {v:k for k,v in USER_GROUP_IDX_TO_NAME.items()}
user_diurnal_df_["USER_GROUP"] = [USER_GROUP_IDX_TO_NAME[val] for val in cluster_result]

user_group = user_diurnal_df_.reset_index().groupby(["USER_GROUP"]).agg(N_USER = ("UID","count"))

In [20]:
fig = go.Figure()

K = 4
keys = [USER_GROUP_NAME_TO_IDX[label] for label in LABEL_ORDER]
for idx, label in enumerate(LABEL_ORDER):
    key = USER_GROUP_NAME_TO_IDX[label]
    fig.add_trace(
        go.Bar(y=[f"User Group {4-idx}(G{4-idx}):<br>{label_}"for idx, label_ in enumerate(list(LABEL_ORDER)[::-1])],
               x=cluster_model.cluster_centers_[keys[::-1], idx],
               name= label + " Pattern",
               orientation='h',
               )
    )
fig.update_layout(
    barmode='stack',
    legend = dict(orientation = 'h', yanchor = 'top', xanchor = "center", x = .5, y = 1.1, font_size = 14, traceorder = 'normal'),
    width = 900,
    height = 600,
    title="Days of Each Diurnal Pattern in Each User Group"
)
fig.show()
fig.write_image(os.path.join(fig_dir,"user_group.svg"))

### Multi-Level Regression for All Variables

In [21]:
user_diurnal_df_["USER_GROUP"] = [str(LABEL_ORDER.index(user_group))+". "+user_group for user_group in user_diurnal_df_["USER_GROUP"].values]
user_diurnal_df_

LABEL  Both Dominant  Phone to Both  Wearable Dominant  Phone Dominant  LABEL  \
UID                                                                             
P001               3             19                  1               8      0   
P002              18              6                  0               7      1   
P004               1              5                  1              24      3   
P006               0              3                 27               1      2   
P007               1              8                  7              15      3   
...              ...            ...                ...             ...    ...   
P122               1             25                  0               5      0   
P124              19              5                  1               6      1   
P125               2              7                 10              12      0   
P126               1             23                  1               6      0   
P127              12              2                  2              15      3   

LABEL            USER_GROUP  
UID                          
P001       1. Phone to Both  
P002       0. Both Dominant  
P004      3. Phone Dominant  
P006   2. Wearable Dominant  
P007      3. Phone Dominant  
...                     ...  
P122       1. Phone to Both  
P124       0. Both Dominant  
P125       1. Phone to Both  
P126       1. Phone to Both  
P127      3. Phone Dominant  

[102 rows x 6 columns]

In [22]:
bout_df["WEEKEND"] = bout_df["DAY_OF_WEEK"] >= 5
bout_df["MVPA_DUT"] = [duration if intensity =="MVPA" else 0 for duration,intensity in bout_df[["DURATION","PA_TYPE"]].values]
bout_df["MPA_DUT"] = [duration if intensity =="MPA" else 0 for duration,intensity in bout_df[["DURATION","PA_TYPE"]].values]
bout_df["VPA_DUT"] = [duration if intensity =="VPA" else 0 for duration,intensity in bout_df[["DURATION","PA_TYPE"]].values]

daily_coverage = bout_df.groupby(["UID","DATE","TYPE"]).agg(STEP = ("AVERAGE_STEP","sum"))
daily_coverage = daily_coverage.unstack(level = 2, fill_value = 0)
daily_coverage.columns = daily_coverage.columns.get_level_values(1) 
daily_coverage = daily_coverage.apply(lambda x: x/np.sum(x), axis = 1)
daily_coverage *= 100
daily_coverage.reset_index(inplace = True)


daily_variables = bout_df.groupby(["UID","DATE", "DAY_OF_WEEK", "WEEKEND"]).agg(DAILY_STEP_COUNT = ("AVERAGE_STEP", "sum"),MVPA_DUT = ('MVPA_DUT', 'sum'), MPA_DUT = ('MPA_DUT', 'sum'), VPA_DUT = ('VPA_DUT', 'sum'))
daily_variables.reset_index(inplace = True)

user_variables = daily_variables.groupby(["UID"]).agg(AVG_DAILY_STEP = ("DAILY_STEP_COUNT", 'mean'))
user_variables.reset_index(inplace = True)

meta = pd.read_csv(os.path.join(data_dir, "meta.csv"))
user_variables = user_variables.merge(meta[["UID", "AGE","GENDER"]], on = ["UID"])

user_variables = user_variables.merge(user_diurnal_df_.reset_index()[["UID","USER_GROUP"]], on = ["UID"])

regression_df = pd.merge(daily_coverage, daily_variables, on = ["UID","DATE"])
regression_df = regression_df.merge(user_variables, on = ["UID"])
regression_df["DAILY_STEP_COUNT"] /= 1000
regression_df["AVG_DAILY_STEP"] /= 1000
regression_df["DAILY_ACTIVE_LEVEL"] = (regression_df["DAILY_STEP_COUNT"].values / regression_df["AVG_DAILY_STEP"].values-1) *100
for col in ["MVPA_DUT", "VPA_DUT", "MPA_DUT"]:
    regression_df[col] /= 60

In [23]:
import statsmodels.api as sm
from sklearn.metrics import r2_score

def get_summary(mdf):
    return pd.DataFrame([mdf.params, mdf.tvalues, mdf.pvalues], index = ["Coef","t", "p"]).T

summary = []
for val in ["BOTH","PHONE","WEARABLE"]:
    md = sm.MixedLM.from_formula(f"{val} ~ C(USER_GROUP) + DAILY_ACTIVE_LEVEL + C(WEEKEND) + MVPA_DUT + VPA_DUT + MPA_DUT + AVG_DAILY_STEP + AGE + C(GENDER)", data = regression_df, groups = "UID")
    mdf = md.fit()

    # Compute the R-square
    y_hat = mdf.predict()
    r2_marginal = r2_score(regression_df[val], y_hat)

    y_hat_conditional = mdf.fittedvalues
    r2_conditional = r2_score(regression_df[val], y_hat_conditional)
    print(val,': Marginal: {:.3f}, Conditional: {:.3f}'.format(r2_marginal, r2_conditional))
    summary_ = get_summary(mdf)
    summary_["sig"] = [show_signifcance(pval) for pval in summary_["p"].values] 
    summary_.columns = pd.MultiIndex.from_product([[val],summary_.columns])
    summary.append(summary_)
summary = pd.concat(summary, axis = 1)
summary = summary.loc[["Intercept","AGE","C(GENDER)[T.M]","AVG_DAILY_STEP",
"C(USER_GROUP)[T.1. Phone to Both]","C(USER_GROUP)[T.2. Wearable Dominant]","C(USER_GROUP)[T.3. Phone Dominant]",
            "C(WEEKEND)[T.True]","DAILY_ACTIVE_LEVEL", "MPA_DUT","MVPA_DUT","VPA_DUT"]]
display(summary)
summary.to_csv(os.path.join(table_dir,"regression_result.csv"))

BOTH : Marginal: 0.341, Conditional: 0.468
PHONE : Marginal: 0.376, Conditional: 0.496
WEARABLE : Marginal: 0.132, Conditional: 0.389


BOTH                           \
                                            Coef          t             p   
Intercept                              56.373378   9.418938  4.556740e-21   
AGE                                     0.064743   0.412476  6.799906e-01   
C(GENDER)[T.M]                         -3.634984  -1.429401  1.528890e-01   
AVG_DAILY_STEP                          1.441064   3.455954  5.483479e-04   
C(USER_GROUP)[T.1. Phone to Both]      -7.841461  -2.284554  2.233899e-02   
C(USER_GROUP)[T.2. Wearable Dominant]  -5.281395  -1.599297  1.097546e-01   
C(USER_GROUP)[T.3. Phone Dominant]    -35.125299  -9.540544  1.420854e-21   
C(WEEKEND)[T.True]                     -7.314669  -7.672852  1.682131e-14   
DAILY_ACTIVE_LEVEL                      0.183237  13.663171  1.684841e-42   
MPA_DUT                                 0.405500   0.552693  5.804738e-01   
MVPA_DUT                                1.505805   0.895551  3.704924e-01   
VPA_DUT                               -14.682824  -2.668847  7.611220e-03   

                                                PHONE                          \
                                       sig       Coef         t             p   
Intercept                              ***  27.123310  4.377813  1.198763e-05   
AGE                                          0.042516  0.261664  7.935807e-01   
C(GENDER)[T.M]                               4.496462  1.708097  8.761841e-02   
AVG_DAILY_STEP                         ***  -0.238526 -0.552517  5.805941e-01   
C(USER_GROUP)[T.1. Phone to Both]        *   2.726378  0.767327  4.428873e-01   
C(USER_GROUP)[T.2. Wearable Dominant]       -8.038953 -2.351632  1.869125e-02   
C(USER_GROUP)[T.3. Phone Dominant]     ***  37.523306  9.845596  7.161342e-23   
C(WEEKEND)[T.True]                     ***   7.662638  7.759695  8.513409e-15   
DAILY_ACTIVE_LEVEL                     ***  -0.100505 -7.235146  4.650273e-13   
MPA_DUT                                     -3.890515 -5.119590  3.062013e-07   
MVPA_DUT                                    -4.753120 -2.728449  6.363287e-03   
VPA_DUT                                 **  -8.168031 -1.433813  1.516255e-01   

                                             WEARABLE                          \
                                       sig       Coef         t             p   
Intercept                              ***  16.478963  3.076894  2.091694e-03   
AGE                                         -0.107381 -0.763768  4.450054e-01   
C(GENDER)[T.M]                              -0.863428 -0.378753  7.048710e-01   
AVG_DAILY_STEP                              -1.193669 -3.353904  7.967994e-04   
C(USER_GROUP)[T.1. Phone to Both]            5.119963  1.664019  9.610866e-02   
C(USER_GROUP)[T.2. Wearable Dominant]    *  13.324195  4.502422  6.718357e-06   
C(USER_GROUP)[T.3. Phone Dominant]     ***  -2.387881 -0.724416  4.688101e-01   
C(WEEKEND)[T.True]                     ***  -0.337656 -0.520520  6.027014e-01   
DAILY_ACTIVE_LEVEL                     ***  -0.082394 -8.983560  2.621437e-19   
MPA_DUT                                ***   3.475341  6.895912  5.352042e-12   
MVPA_DUT                                **   3.119639  2.714296  6.641687e-03   
VPA_DUT                                     23.034460  6.122324  9.222037e-10   

                                            
                                       sig  
Intercept                               **  
AGE                                         
C(GENDER)[T.M]                              
AVG_DAILY_STEP                         ***  
C(USER_GROUP)[T.1. Phone to Both]           
C(USER_GROUP)[T.2. Wearable Dominant]  ***  
C(USER_GROUP)[T.3. Phone Dominant]          
C(WEEKEND)[T.True]                          
DAILY_ACTIVE_LEVEL                     ***  
MPA_DUT                                ***  
MVPA_DUT                                **  
VPA_DUT                                ***